# First pass: waypoint detection

We will pass through all trajectories in order to obtain all the turning points, write them down to a CSV file

<span style="color:red">CAUTION: Do not run all cells in this notebook.</span>

In [2]:
import numpy as np 
from matplotlib import pyplot as plt
import os
from get_turn import load_turnandrise_from_zarr, TurnAndRise
import pandas as pd

In [3]:
# List all files in the '../data/osstate/routes/' directory
date_folders = os.listdir('../data/osstate/routes/')
date_folders.sort()
print('There are {} date folders in the ../data/osstate/routes/ directory'.format(len(date_folders)))

There are 84 date folders in the ../data/osstate/routes/ directory


In [4]:
import random
import string

def generate_random_string(length = 12):
    letters = string.ascii_letters + string.digits
    return ''.join(random.choice(letters) for _ in range(length))

In [10]:
def process_folder(folder_path: str) -> None:
    
    # List all files in the folder
    files = os.listdir(folder_path)
    files.sort()
    print('There are {} files in the folder {}'.format(len(files), folder_path))
    # Create a CSV file to store waypoints
    csv_file_wp = open(folder_path + '/waypoints.csv', 'w')
    # raise Exception('Waypoint path is: {}'.format(folder_path + '/waypoints.csv'))
    csv_file_wp.write('ident, lat, lon')
    
    # Load the data from the files
    for file in files:
        file_path = os.path.join(folder_path, file)
        # if file does not end in .zarr, skip
        if not file_path.endswith('.zarr'):
            continue
        try:
            turn_and_rise:TurnAndRise = load_turnandrise_from_zarr(file_path)
            if 'AAL1087' in file_path:
                print('Stop here')
            # Create a CSV file to store the route for each flight
            # print('Route path is: {}'.format(file_path + '_route.csv'))
            print('Route path is: {}'.format(file_path + '_route.csv'))
            csv_file_route = open(file_path + '_route.csv', 'w')
            csv_file_route.write('ident')
            for i in range(len(turn_and_rise['tp_lat'])):
                wp_ident = generate_random_string()
                csv_file_wp.write('\n' + wp_ident + ', ' + str(turn_and_rise['tp_lat'][i]) + ', ' + str(turn_and_rise['tp_lon'][i]))
                csv_file_route.write('\n' + wp_ident)
            csv_file_route.close()
        except Exception as e:
            print('Error processing file {}. Skip.'.format(file_path))
            print(e)
            if csv_file_route:
                csv_file_route.close()
            continue 
        
    csv_file_wp.close()

# List all folders in routes
for folder in date_folders:
    print('Processing folder {}'.format(folder))
    process_folder('../data/osstate/routes/' + folder)

Processing folder states_2022-01-03-00.csv
There are 1501 files in the folder ../data/osstate/routes/states_2022-01-03-00.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/3461_aa1635.zarr_route.csv


Stop here
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL1087_ad6758.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL1158_ac77d3.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL1165_a8d5bd.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL1242_abedc8.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL1288_adc8e7.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL1333_a35aae.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL1355_a95665.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL1385_abc292.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL145_aaa326.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.csv/AAL1473_aa0aab.zarr_route.csv
Route path is: ../data/osstate/routes/states_2022-01-03-00.cs

# Second pass

Merging the routes of dangling flights

In [5]:
from typing import List

In [6]:
def merge_dangling() -> None: 
    # List all folders in the '../data/osstate/routes/' directory
    date_folders = os.listdir('../data/osstate/routes/')
    date_folders.sort()
    print('date folders: {}'.format(date_folders))
    # date_folders: ['states_2022-01-03-00.csv', 'states_2022-01-03-01.csv',...]
    print('There are {} date folders in the ../data/osstate/routes/ directory'.format(len(date_folders)))
    for folder_no, folder in enumerate(date_folders):
        if folder_no == 0:
            continue # Skip the first folder
        preceding_folder_name = date_folders[folder_no - 1]
        dangling_csv_filename = preceding_folder_name + '.csv' # should be states_2022-01-03-00.csv.csv
        dangling_df = pd.read_csv('../data/osstate/dangling/' + dangling_csv_filename)
        dangling_idents = dangling_df['ident'].unique().tolist()
        
        # List all ZARR subfolders in the folder
        files = os.listdir('../data/osstate/routes/' + folder)
        # files: 'UAE76F_896481.zarr_route.csv', 'UAE76F_896482.zarr', ...
        # Only keep the ZARR subfolders
        zarr_files = [f for f in files if f.endswith('.zarr')]
        zarr_files.sort()
        # zarr_files: 'UAE76F_896481.zarr'...
        # Open the dangling ident instruction csv file
        for zarr_file in zarr_files:
            # Strip the '.zarr' extension
            flight_ident = zarr_file[:-5]
            # Check if the flight_ident is in the dangling_idents
            if flight_ident in dangling_idents:
                # Open the route csv file
                print('Found a dangling ident: {}'.format(flight_ident))
                
                current_route_csv_file = open('../data/osstate/routes/' + folder + '/' + zarr_file + '_route.csv', 'r')
                preceding_route_csv_file = open('../data/osstate/routes/' + preceding_folder_name + '/' + flight_ident + '.zarr_route.csv', 'r')
                
                # print('current_route_csv_file: {}'.format(current_route_csv_file))
                # print('preceding_route_csv_file: {}'.format(preceding_route_csv_file))
                # return
                
                # Copy the whole preceding route csv file to the current route csv file
                preceding_text = preceding_route_csv_file.read() # Read the whole preceding route csv file
                current_text = current_route_csv_file.read() # Read the whole current route csv file
                preceding_route_csv_file.close() # close the file before reopening in write mode
                # Delete the first line of the current_text
                current_text = current_text[current_text.index('\n') + 1:]
                current_text = preceding_text + current_text # concatenate the preceding_text and current_text
                current_route_csv_file = open('../data/osstate/routes/' + folder + '/' + zarr_file + '_route.csv', 'w')
                current_route_csv_file.write(current_text)
                # raise Exception('STOP HERE PLEASE! Verify before proceeding!')
                print('Merge completed for flight {}'.format(flight_ident))
                current_route_csv_file.close()
                preceding_route_csv_file.close()
                
                
            
merge_dangling()
        

date folders: ['states_2022-01-03-00.csv', 'states_2022-01-03-01.csv', 'states_2022-01-03-02.csv', 'states_2022-01-03-03.csv', 'states_2022-01-03-04.csv', 'states_2022-01-03-05.csv', 'states_2022-01-03-06.csv', 'states_2022-01-03-07.csv', 'states_2022-01-03-08.csv', 'states_2022-01-03-09.csv', 'states_2022-01-03-10.csv', 'states_2022-01-03-11.csv', 'states_2022-01-03-12.csv', 'states_2022-01-03-13.csv', 'states_2022-01-03-14.csv', 'states_2022-01-03-15.csv', 'states_2022-01-03-16.csv', 'states_2022-01-03-17.csv', 'states_2022-01-03-18.csv', 'states_2022-01-03-19.csv', 'states_2022-01-03-20.csv', 'states_2022-01-03-21.csv', 'states_2022-01-03-22.csv', 'states_2022-01-03-23.csv', 'states_2022-01-10-00.csv', 'states_2022-01-10-01.csv', 'states_2022-01-10-02.csv', 'states_2022-01-10-03.csv', 'states_2022-01-10-04.csv', 'states_2022-01-10-05.csv', 'states_2022-01-10-06.csv', 'states_2022-01-10-07.csv', 'states_2022-01-10-08.csv', 'states_2022-01-10-09.csv', 'states_2022-01-10-10.csv', 'stat